
- Grupo 2 Robinson Marin Moralez, Guillermo Leon Loaiza Mesa

dataset  https://www.kaggle.com/datasets/dansbecker/powerlifting-database?resource=download 

In [0]:
!pip install kagglehub
!kagglehub[pandas-datasets]>-0.3.8
!restart_python

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
/bin/bash: line 1: kagglehub[pandas-datasets]: command not found
/bin/bash: line 1: restart_python: command not found


### importacion de librerias

In [0]:
import kagglehub
import pandas as pd
import os
import zipfile

In [0]:
%pip install ingestar
%restart_python
from ingestar import Ingestar 




Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


---------------------------------------------------------------------------
ImportError                               Traceback (most recent call last)
File <command-7186756751571284>, line 3
      1 get_ipython().run_line_magic('pip', 'install ingestar')
      2 get_ipython().run_line_magic('restart_python', '')
----> 3 from ingestar import Ingestar

ImportError: cannot import name 'Ingestar' from 'ingestar' (/local_disk0/.ephemeral_nfs/envs/pythonEnv-f86f5956-7a3f-43e7-8ce0-bcb04a3b02a5/lib/python3.12/site-packages/ingestar/__init__.py)

In [0]:

def download_dataset_zip(url = ""):
        print("Descargando dataset desde Kaggle...")
        dataset_path = kagglehub.dataset_download(url)
        print("Ruta al dataset:", dataset_path)
        return dataset_path
    
def extract_zip_files(dataset_path):
        zip_files = [f for f in os.listdir(dataset_path) if f.endswith('.zip')]
        if zip_files:
            zip_file = os.path.join(dataset_path, zip_files[0])
            extract_dir = os.path.join(dataset_path, "extracted")
            os.makedirs(extract_dir, exist_ok=True)
            print(f"Extrayendo {zip_file} en {extract_dir}...")
            with zipfile.ZipFile(zip_file, "r") as z:
                z.extractall(extract_dir)
            return extract_dir
        else:
            # Si no se encuentra un ZIP, se verifica si existen archivos CSV en la ruta
            csv_files = [f for f in os.listdir(dataset_path) if f.endswith('.csv')]
            if csv_files:
                print("No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.")
                return dataset_path
            else:
                raise FileNotFoundError("No se encontró ningún archivo .zip ni archivos .csv en la ruta del dataset")

def create_csv(csv_dir):
        #os.makedirs('src/static/csv', exist_ok=True)
        csv_files = [f for f in os.listdir(csv_dir) if f.endswith('.csv')]
        if not csv_files:
            raise FileNotFoundError("No se encontraron archivos CSV en el directorio extraído")

        for file in csv_files:
            file_path = os.path.join(csv_dir, file)
            print(f"Leyendo {file_path}...")
            try:
                df = pd.read_csv(file_path, encoding="latin1")
            except Exception as e:
                print(f"Error al leer {file}: {e}")
                continue
            print(f"Creando/actualizando ")
        print("cvs creado correctamente en ")
        return df
     

extraemos los archivos del dataset

In [0]:
df = pd.DataFrame()
dataset = download_dataset_zip("dansbecker/powerlifting-database") 
csv_dir =extract_zip_files(dataset)
df = create_csv(csv_dir)

Descargando dataset desde Kaggle...


100%|██████████| 8.85M/8.85M [00:00<00:00, 66.8MB/s]

Extracting files...


Ruta al dataset: /home/spark-4106b048-5e99-4617-8137-2f/.cache/kagglehub/datasets/dansbecker/powerlifting-database/versions/1
No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.
Leyendo /home/spark-4106b048-5e99-4617-8137-2f/.cache/kagglehub/datasets/dansbecker/powerlifting-database/versions/1/meets.csv...
Creando/actualizando 
Leyendo /home/spark-4106b048-5e99-4617-8137-2f/.cache/kagglehub/datasets/dansbecker/powerlifting-database/versions/1/openpowerlifting.csv...
Creando/actualizando 
cvs creado correctamente en 


In [0]:
df.head(2)

MeetID              Name Sex  ... TotalKg  Place   Wilks
0       0  Angie Belk Terry   F  ...  138.35      1  155.05
1       0       Dawn Bogart   F  ...  401.42      1  456.38

[2 rows x 17 columns]

convert df pandas to spartk

In [0]:
spark_df = spark.createDataFrame(df)

creamos la tabla con una vista temporal

In [0]:
spark_df.createTempView("competidor_powerlifting")
display(spark_df)


MeetID Name Sex Equipment Age Division BodyweightKg WeightClassKg Squat4Kg BestSquatKg Bench4Kg BestBenchKg Deadlift4Kg BestDeadliftKg TotalKg Place Wilks 0 Angie Belk Terry F Wraps 47.0 Mst 45-49 59.6 60 null 47.63 null 20.41 null 70.31 138.35 1 155.05 0 Dawn Bogart F Single-ply 42.0 Mst 40-44 58.51 60 null 142.88 null 95.25 null 163.29 401.42 1 456.38 0 Dawn Bogart F Single-ply 42.0 Open Senior 58.51 60 null 142.88 null 95.25 null 163.29 401.42 1 456.38 0 Dawn Bogart F Raw 42.0 Open Senior 58.51 60 null null null 95.25 null null 95.25 1 108.29 0 Destiny Dula F Raw 18.0 Teen 18-19 63.68 67.5 null null null 31.75 null 90.72 122.47 1 130.47 0 Courtney Norris F Wraps 28.0 Open Senior 62.41 67.5 -183.7 170.1 null 77.11 null 145.15 392.36 1 424.4 0 Maureen Clary F Raw 60.0 Mst 60-64 67.31 67.5 null 124.74 null 95.25 null 163.29 383.28 1 391.98 0 Maureen Clary F Raw 60.0 Open Senior 67.31 67.5 null 124.74 null 95.25 null 163.29 383.28 1 391.98 0 Priscilla Sweat Pardue F Wraps 52.0 50-54 65.95 67.5 null 120.2 null 54.43 null 108.86 283.49 1 294.25 0 Priscilla Sweat Pardue F Raw 52.0 Senior 65.95 67.5 null null null null null 108.86 108.86 1 112.99 0 Kayce Hoover F Wraps 24.0 Junior 65.5 67.5 null 138.35 null 65.77 null 136.08 340.2 1 354.89 0 Cindy Meeker F Wraps 56.0 Mst 55-59 71.21 75 null 120.2 null 43.09 null 129.27 292.56 1 287.67 0 Cindy Meeker F Wraps 56.0 Open Senior 71.21 75 null 120.2 null 43.09 null 129.27 292.56 1 287.67 0 Candice Pardue Maness F Wraps 54.0 Mst 50-54 70.58 75 null 102.06 null 74.84 null 106.59 283.49 1 280.44 0 Danielle Ortiz F Raw 17.0 Teen 16-17 69.31 75 null 81.65 null 49.9 null 115.67 247.22 1 247.64 0 Jessica Jenkins F Multi-ply 32.0 Open Senior 80.56 82.5 null 229.06 null 161.03 null 210.92 601.01 1 547.81 0 Jessica Wissmann F Wraps 25.0 Open Senior 77.93 82.5 null 142.88 null 68.04 null 136.08 347.0 1 322.3 0 Emma Love F Raw 18.0 Teen 18-19 77.93 82.5 null 86.18 null 52.16 null 83.91 222.25 1 206.43 0 Kelly Benson F Raw 22.0 Open Junior 88.72 90 null 102.06 null 77.11 null 120.2 299.37 1 260.25 0 Cathy Cranford F Raw 56.0 Mst 55-59 83.1 90 null 86.18 null 38.56 null 102.06 226.8 1 203.35 0 Alexis Eliopoulos F Wraps 30.0 Senior 88.36 90 -183.7 174.63 null 122.47 204.12 195.04 492.14 1 428.59 0 Shannon Nash F Raw 44.0 Open Senior 83.64 90 null null null 165.56 null null 165.56 1 147.95 0 Paula Bowers F Wraps 34.0 Open Junior 94.8 90+ null 74.84 null 47.63 null 92.99 215.46 1 182.5 0 Kevin Gingerich M Raw 32.0 Open Junior 71.94 75 null 154.22 null 115.67 null 183.7 453.59 2 333.01 0 Juan Bollo M Raw 20.0 Open Junior 70.67 75 null 163.29 null 111.13 null 204.12 478.54 1 356.03 0 James McManus M Wraps 36.0 Open Junior 74.93 75 null null null null null null null DQ null 0 James McManus M Raw 36.0 Open Junior 74.93 75 null null null 115.67 null 156.49 272.16 1 194.06 0 Scott Faircloth M Wraps 27.0 Open M/P/F 71.3 75 null 181.44 null 99.79 null 188.24 469.47 1 346.96 0 Justin Monk M Raw 22.0 Open Junior 79.65 82.5 null 161.03 null 127.01 null 197.31 485.35 2 332.27 0 Kevin Londe M Raw 23.0 Open Junior 80.1 82.5 null 190.51 null 120.2 null 231.33 542.04 1 369.76 0 Brandon Plyler M Wraps 27.0 Open Junior 76.66 82.5 null 165.56 null 124.74 null 201.85 492.15 1 345.47 0 Scott Terry M Multi-ply 49.0 Mst 45-49 79.11 82.5 null 254.01 null 131.54 null 219.99 605.54 1 416.35 0 Matt Borquez M Wraps 28.0 Open Senior 81.47 82.5 null 258.55 null 174.63 null 240.4 673.58 1 454.68 0 Michael Mahaffey M Raw 42.0 Mst 40-44 81.92 82.5 null 233.6 null 154.22 null 247.21 635.03 1 427.22 0 Michael Mahaffey M Raw 42.0 Open Senior 81.92 82.5 null 233.6 null 154.22 null 247.21 635.03 1 427.22 0 Tanner Huntley M Raw 21.0 Open Junior 86.55 90 null 206.38 null 115.67 null 260.82 582.87 1 379.87 0 Corey McManus M Raw 40.0 Mst 40-44 88.54 90 null 215.46 null 192.78 null 251.74 659.98 1 424.91 0 Jake Reed M Wraps 23.0 Open Senior 88.9 90 null 233.6 null 142.88 null 256.28 632.76 2 406.52 0 Randy Rabon M Wraps 28.0 Open Senior 88.99 90 

In [0]:
%sql
select count (*) from competidor_powerlifting

count(*) 386414

Se muestra la evidencia de la carga con un select * limit 5

In [0]:
%sql
SELECT * FROM competidor_powerlifting 
LIMIT 5

MeetID Name Sex Equipment Age Division BodyweightKg WeightClassKg Squat4Kg BestSquatKg Bench4Kg BestBenchKg Deadlift4Kg BestDeadliftKg TotalKg Place Wilks 0 Angie Belk Terry F Wraps 47.0 Mst 45-49 59.6 60 null 47.63 null 20.41 null 70.31 138.35 1 155.05 0 Dawn Bogart F Single-ply 42.0 Mst 40-44 58.51 60 null 142.88 null 95.25 null 163.29 401.42 1 456.38 0 Dawn Bogart F Single-ply 42.0 Open Senior 58.51 60 null 142.88 null 95.25 null 163.29 401.42 1 456.38 0 Dawn Bogart F Raw 42.0 Open Senior 58.51 60 null null null 95.25 null null 95.25 1 108.29 0 Destiny Dula F Raw 18.0 Teen 18-19 63.68 67.5 null null null 31.75 null 90.72 122.47 1 130.47

creamos tabla permanente verificamos en catalogo 

In [0]:
spark_df.write.mode("overwrite").saveAsTable("tbl_competidor_powerlifting") #overwrite sobreescribe el contenido de la tabla, append agregaal final, errorifexists lanza error
display(spark_df)

MeetID MeetPath Federation Date MeetCountry MeetState MeetTown MeetName 0 365strong/1601 365Strong 2016-10-29 USA NC Charlotte 2016 Junior & Senior National Powerlifting Championships 1 365strong/1602 365Strong 2016-11-19 USA MO Ozark Thanksgiving Powerlifting Classic 2 365strong/1603 365Strong 2016-07-09 USA NC Charlotte Charlotte Europa Games 3 365strong/1604 365Strong 2016-06-11 USA SC Rock Hill Carolina Cup Push Pull Challenge 4 365strong/1605 365Strong 2016-04-10 USA SC Rock Hill Eastern USA Challenge 5 365strong/1701 365Strong 2017-04-22 USA NC Charlotte Charlotte Europa Games 6 365strong/1702 365Strong 2017-01-21 USA GA Martinez New Year Challenge 7 365strong/1703 365Strong 2017-06-10 USA MO Lake Ozark Midwest Regionals 8 365strong/1704 365Strong 2017-07-15 USA SC Rock Hill Victory Cup Challenge 9 365strong/1705 365Strong 2017-08-12 USA NC Fayetteville Eastern Regional Championship 10 365strong/1706 365Strong 2017-09-30 USA IN Evansville Ohio Valley Regional Open Powerlifting Championships 11 365strong/1707 365Strong 2017-09-30 USA IN Evansville US Masters Open 12 365strong/1708 365Strong 2017-10-28 USA NC Charlotte 2017 Men & Women National Powerlifting Championships 13 365strong/1709 365Strong 2017-12-09 USA SC Conway East Coast Conflict 14 aau/1601 AAU 2016-07-09 USA CA San Jose Kindred NorCal Powerlifting Championships 15 aau/1602 AAU 2016-09-23 USA NV Las Vegas 2016 AAU Worlds 16 aau/1701 AAU 2017-02-25 USA CA San Diego So Cal Meet 17 aau/1702 AAU 2017-05-20 USA CA Los Angeles Battle of Los Angeles 18 aau/1703 AAU 2017-02-11 USA CA Santa Barbara Central California Meet 19 aau/1704 AAU 2017-03-18 USA CA Santa Clara American Meet 20 aau/1705 AAU 2017-01-21 USA NV Las Vegas Sin City Powerlifting 21 adfpa/9501 ADFPA 1995-07-15 USA PA Wilkes-Barre Men's Nationals 22 apa/1001 APA 2010-11-13 USA FL null Ironfest Challenge 23 apa/1002 APA 2010-04-17 USA null null Raw Nationals 24 apa/1401 APA 2014-10-04 USA OR Portland Elite Fall Classic 25 apa/1601 APA 2016-01-30 USA OR Portland APA Winter Classic 26 apa/1602 APA 2016-04-16 USA OR Clackamas Elite Spring Challenge District 7 Regionals 27 apa/1701 APA 2017-01-21 USA AK Searcy Rhino Open Championships 28 apa/1702 APA 2017-08-05 USA MI Metamora Michigan Summer Iron Bash 29 apa/1703 APA 2017-07-29 USA AL Tuscaloosa Raw Wars III 30 apa/1704 APA 2017-07-22 USA MO Ellisville Missouri Raw Summer Iron Bash 31 apa/1705 APA 2017-07-15 USA TX El Paso Lone Star Raw Championships 32 apa/1706 APA 2017-05-20 USA OH Lebanon Raw Nationals 33 apa/1707 APA 2017-07-08 USA AR Newport Southern States 34 apa/1708 APA 2017-06-17 USA NJ Hillsborough Garden State Raw Championships 35 apa/1709 APA 2017-06-10 USA AR Harrison Clash of the Iron Warriors 36 apa/1710 APA 2017-05-20 USA FL Largo Blessed Iron Bash 37 apa/1711 APA 2017-05-13 USA MS Philadelphia Mississippi State Championships 38 apa/1712 APA 2017-05-13 USA VT Brattleboro 30th Can-Am International Championships 39 apa/1713 APA 2017-04-15 USA TX McAllen Region 6 Championships 40 apa/1714 APA 2017-04-01 USA TX El Paso Sun City Championships 41 apa/1715 APA 2017-02-18 USA AR Harrison Arkansas Raw Championships 42 apa/1716 APA 2017-08-19 USA AR Conway Battle of the Badasses 43 apa/1717 APA 2017-09-02 USA MO Leadington Ozark Open 44 apa/1718 APA 2017-04-22 USA MO Jackson ShowMe State Raw Championships 45 apa/1719 APA 2017-03-25 USA UT St. George Utah Open Raw Championships 46 apa/1720 APA 2017-01-21 USA FL Largo Thunderbay Throwdown 47 apa/1721 APA 2017-10-07 USA TX Weslaco US Open 48 apa/1722 APA 2017-09-23 USA UT St. George West Coast Raw Championships 49 apa/1723 APA 2017-09-16 USA MI Clawson 4th Annual Wolverine Open Raw Championships 50 apa/1724 APA 2017-12-09 USA AR Harrison Rocky Memorial VIII 51 apa/1725 APA 2017-02-11 USA MS Philadelphia Magnolia Open Championships 52 apa/1726 APA 2017-01-21 USA OR Portland Winter Classic 53 apa/1727 APA 2017-02-25 USA MO Park Hills District 5 Regional Championships 54 apa/1728 APA 2017-03-18 USA MI St. J

Consultas a la db en la tabla tbl_competidor_powerlifting

In [0]:
%sql
DESCRIBE TABLE tbl_competidor_powerlifting;

col_name data_type comment MeetID bigint null MeetPath string null Federation string null Date string null MeetCountry string null MeetState string null MeetTown string null MeetName string null

In [0]:
%sql
select count (*) from tbl_competidor_powerlifting

count(*) 8482

In [0]:
%sql
SELECT * FROM tbl_competidor_powerlifting WHERE Federation = 'APA';

MeetID MeetPath Federation Date MeetCountry MeetState MeetTown MeetName 22 apa/1001 APA 2010-11-13 USA FL null Ironfest Challenge 23 apa/1002 APA 2010-04-17 USA null null Raw Nationals 24 apa/1401 APA 2014-10-04 USA OR Portland Elite Fall Classic 25 apa/1601 APA 2016-01-30 USA OR Portland APA Winter Classic 26 apa/1602 APA 2016-04-16 USA OR Clackamas Elite Spring Challenge District 7 Regionals 27 apa/1701 APA 2017-01-21 USA AK Searcy Rhino Open Championships 28 apa/1702 APA 2017-08-05 USA MI Metamora Michigan Summer Iron Bash 29 apa/1703 APA 2017-07-29 USA AL Tuscaloosa Raw Wars III 30 apa/1704 APA 2017-07-22 USA MO Ellisville Missouri Raw Summer Iron Bash 31 apa/1705 APA 2017-07-15 USA TX El Paso Lone Star Raw Championships 32 apa/1706 APA 2017-05-20 USA OH Lebanon Raw Nationals 33 apa/1707 APA 2017-07-08 USA AR Newport Southern States 34 apa/1708 APA 2017-06-17 USA NJ Hillsborough Garden State Raw Championships 35 apa/1709 APA 2017-06-10 USA AR Harrison Clash of the Iron Warriors 36 apa/1710 APA 2017-05-20 USA FL Largo Blessed Iron Bash 37 apa/1711 APA 2017-05-13 USA MS Philadelphia Mississippi State Championships 38 apa/1712 APA 2017-05-13 USA VT Brattleboro 30th Can-Am International Championships 39 apa/1713 APA 2017-04-15 USA TX McAllen Region 6 Championships 40 apa/1714 APA 2017-04-01 USA TX El Paso Sun City Championships 41 apa/1715 APA 2017-02-18 USA AR Harrison Arkansas Raw Championships 42 apa/1716 APA 2017-08-19 USA AR Conway Battle of the Badasses 43 apa/1717 APA 2017-09-02 USA MO Leadington Ozark Open 44 apa/1718 APA 2017-04-22 USA MO Jackson ShowMe State Raw Championships 45 apa/1719 APA 2017-03-25 USA UT St. George Utah Open Raw Championships 46 apa/1720 APA 2017-01-21 USA FL Largo Thunderbay Throwdown 47 apa/1721 APA 2017-10-07 USA TX Weslaco US Open 48 apa/1722 APA 2017-09-23 USA UT St. George West Coast Raw Championships 49 apa/1723 APA 2017-09-16 USA MI Clawson 4th Annual Wolverine Open Raw Championships 50 apa/1724 APA 2017-12-09 USA AR Harrison Rocky Memorial VIII 51 apa/1725 APA 2017-02-11 USA MS Philadelphia Magnolia Open Championships 52 apa/1726 APA 2017-01-21 USA OR Portland Winter Classic 53 apa/1727 APA 2017-02-25 USA MO Park Hills District 5 Regional Championships 54 apa/1728 APA 2017-03-18 USA MI St. John's Michigan Open Championships